https://psa.gov.ph/content/functional-difficulty-philippines-household-population-five-years-old-and-over-2020-census
link of dataset
https://data.humdata.org/dataset/philippines-population-projection-2020-2025-admin3 



In [1]:
import pandas as pd 
import numpy as np
import os
import re
import warnings
import json
warnings.filterwarnings("ignore")
pwd=os.getcwd()
dataset = pd.read_csv(pwd + r"/csv/functional_difficulty.csv", encoding="ISO-8859-1")
total_population=pd.read_csv(pwd + r"/csv/ph_population_2020.csv", encoding="ISO-8859-1")



In [2]:
import json
jsonfile = json.load(open(r'geojson/regions/regions.0.01.json'))
jsonfile

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'geometry': {'type': 'MultiPolygon',
    'coordinates': [[[[119.46876076500007, 4.59360219000007],
       [119.47067155200011, 4.591166862000023],
       [119.47015445700004, 4.589235613000028],
       [119.46854112900007, 4.587965888000042],
       [119.46706948200006, 4.58739924300005],
       [119.46568145300012, 4.588041928000052],
       [119.46740658400006, 4.58934240800005],
       [119.46798132900005, 4.592292717000021],
       [119.46876076500007, 4.59360219000007]]],
     [[[119.4701593850001, 4.602214924000066],
       [119.47156420400006, 4.600450677000026],
       [119.47197860300003, 4.598650792000058],
       [119.47066480100011, 4.597888498000032],
       [119.46899530700011, 4.5987716230000615],
       [119.46771223000007, 4.598955704000048],
       [119.46908694700005, 4.602288766000072],
       [119.4701593850001, 4.602214924000066]]],
     [[[119.38482335100002, 4.6260989900000595],
       [119.38621

In [3]:
dataset.dropna().drop_duplicates()
dataset=dataset.drop(dataset[~dataset["Status"].isin(['All', 'Mild', 'Moderate', 'Severe'])].index)

In [4]:
dataset.info()
dataset.describe()

<class 'pandas.core.frame.DataFrame'>
Index: 118292 entries, 0 to 118296
Data columns (total 29 columns):
 #   Column                                                                Non-Null Count   Dtype 
---  ------                                                                --------------   ----- 
 0   Region                                                                118292 non-null  object
 1   Province                                                              118292 non-null  object
 2   Mun                                                                   118292 non-null  object
 3   RegCode_New                                                           118292 non-null  object
 4   RegCode_Old                                                           118292 non-null  object
 5   ProvCode_New                                                          118292 non-null  object
 6   ProvCode_Old                                                          117716 non-null  object
 7 

Age 5-9     Age 10-14    Age 15 - 19    Age 20 - 24  \
count  118292.000000  118292.00000  118292.000000  118292.000000   
mean        7.263044       7.42434       8.683664      10.451966   
std        26.809068      34.41203      54.772227      72.883309   
min         0.000000       0.00000       0.000000       0.000000   
25%         1.000000       1.00000       1.000000       1.000000   
50%         2.000000       2.00000       2.000000       2.000000   
75%         6.000000       6.00000       6.000000       7.000000   
max      1814.000000    3089.00000    5248.000000    6838.000000   

         Age 25 - 29    Age 30 - 34    Age 35 - 39    Age 40 - 44  \
count  118292.000000  118292.000000  118292.000000  118292.000000   
mean       11.257363      11.920544      13.559801      23.332533   
std        75.869223      72.019236      76.125514     136.689187   
min         0.000000       0.000000       0.000000       0.000000   
25%         1.000000       1.000000       1.000000       1.000000   
50%         2.000000       3.000000       3.000000       3.000000   
75%         7.000000       8.000000       9.000000      12.000000   
max      7245.000000    6517.000000    6357.000000   10443.000000   

         Age 45 - 49    Age 50 - 54    Age 55 - 59    Age 60 - 64  \
count  118292.000000  118292.000000  118292.000000  118292.000000   
mean       32.820749      41.972069      45.425861      51.945829   
std       195.608401     241.392551     242.343841     249.503966   
min         0.000000       0.000000       0.000000       0.000000   
25%         1.000000       1.000000       1.000000       1.000000   
50%         3.000000       4.000000       5.000000       7.000000   
75%        15.000000      21.000000      25.000000      34.000000   
max     16164.000000   19872.000000   20334.000000   20893.000000   

         Age 65 - 69    Age 70 - 74    Age 75 - 79  Age 80 years and over  
count  118292.000000  118292.000000  118292.000000          118292.000000  
mean       48.636155      45.023535      35.799065              57.706827  
std       204.218072     166.669915     115.979131             160.509864  
min         0.000000       0.000000       0.000000               0.000000  
25%         2.000000       2.000000       2.000000               6.000000  
50%         7.000000       9.000000       9.000000              19.000000  
75%        36.000000      38.000000      34.000000              59.000000  
max     17443.000000   14032.000000   10714.000000           11525.000000

In [5]:
dataset["Status"].unique()

array(['All', 'Mild', 'Moderate', 'Severe'], dtype=object)

In [6]:
code_to_keep = [x for x in dataset.columns if not re.match(r"^.*(Mun|MunCode_New|Old)$", x)]
#combine agekeep with this using and
dataset=dataset[code_to_keep]

In [7]:
age={"Age: 5-19":["Age 5-9","Age 10-14","Age 15 - 19"],
                        "Age: 20-34":["Age 20 - 24","Age 25 - 29","Age 30 - 34"],
                        "Age: 35–54":["Age 35 - 39","Age 40 - 44","Age 45 - 49","Age 50 - 54"],
                        "Age: 55-80+":["Age 55 - 59","Age 60 - 64","Age 65 - 69","Age 70 - 74","Age 75 - 79",'Age 80 years and over']
                        }
for col_age,age_value in age.items():
    existing=[col for col in age_value if col in dataset.columns]
    dataset[col_age]=dataset[age_value].sum(axis=1)
  

    
#try combine this in for loop for more effiencent 
#dont every use gpt next time even unless its taking you 1 hour and your stuck or you got a error you never got before but you are allowed to
#search but its it not an error just keep tryingif you think you can do it and you just need more time to think then wiat for 1 hours  before 
#gpt in those time think hard on how to solve the problem this is for your future (improve your creativity and problem solving skill)

In [8]:

age_to_keep = [x for x in dataset.columns if not re.match(r"^(\bAge \b).*", x)]
dataset=dataset[age_to_keep]
age_to_keep


['Region',
 'Province',
 'RegCode_New',
 'ProvCode_New',
 'Disability',
 'Sex',
 'Status',
 'Household Population 5 Years Old and Over with Functional Difficulty',
 'Age: 5-19',
 'Age: 20-34',
 'Age: 35–54',
 'Age: 55-80+']

In [9]:
dataset["Disability"]=dataset["Disability"].str.strip()
rename={"Visual Disability":'Seeing even if wearing eyeglasses',
                        "Hearing Disability":'Hearing even if using a hearing aid',
                        "Mobility Disability":'Walking or climbing steps',
                        "Cognitive Disability":'Remembering or concentrating',
                        "Self-Care Disability":'Self-caring (washing all over or dressing)',
                        "Communication Disability":"Communicating"}
for Disability_new,Disability_old in rename.items():
   check=[col for col in Disability_old if col in dataset]
   dataset["Disability"].replace({Disability_old:Disability_new},inplace=True)


In [10]:
to_category=["Region",
                        "Province",
                        "Disability"
                      
                      ]
for x in to_category:
    to_unique=[region_code for region_code in dataset[x].unique()]
    dataset[x]=pd.CategoricalIndex(dataset[x], categories=to_unique,ordered=True)


In [11]:
to_int64=[x for x in dataset.columns]

for x in to_int64:
    dataset[x]=dataset[x].convert_dtypes()



In [12]:
to_numeric = [x for x in dataset.columns if re.match(r"^(\bAge|Ho).*", x)]
to_numeric
for x in to_numeric:
    dataset[x]=pd.to_numeric(dataset[x],errors="coerce").fillna(0).astype("int64")

In [13]:
dataset.loc[117937] #just dont show that you drop this column

Region                                                                  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...
Province                                                                                                 INTERIM PROVINCE
RegCode_New                                                                                                  PH1900000000
ProvCode_New                                                                                                 PH1999900000
Disability                                                                                              Visual Disability
Sex                                                                                                            Both Sexes
Status                                                                                                                All
Household Population 5 Years Old and Over with Functional Difficulty                                                    0
Age: 5-19               

In [14]:
total_population_region=total_population.groupby("Region",as_index=False)["Population"].sum()
total_population_region["Region"]=total_population_region["Region"].str.strip("")
total_population_region

Region  Population
0   BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...     4183315
1              Cordillera Administrative Region (CAR)     1807739
2                                     MIMAROPA Region     3174856
3                       National Capital Region (NCR)    13804656
4                            REGION XI (DAVAO REGION)     5290867
5                           REGION XII (SOCCSKSARGEN)     4919935
6                            Region I (Ilocos Region)     5270807
7                          Region II (Cagayan Valley)     3657746
8                          Region III (Central Luzon)    12313714
9                            Region IV-A (CALABARZON)    16057291
10                    Region IX (Zamboanga Peninsula)     3782761
11                            Region V (Bicol Region)     6133835
12                        Region VI (Western Visayas)     7904895
13                       Region VII (Central Visayas)     7957045
14                      Region VIII (Eastern Visayas)     4742342
15                       Region X (Northern Mindanao)     5017050
16                               Region XIII (Caraga)     2753107

In [15]:
disability_by_region = (
    dataset.loc[(dataset["Sex"] == "Both Sexes")& (dataset["Status"] != "All") ]
    .groupby(["Disability", "Region","Status"], as_index=False)["Household Population 5 Years Old and Over with Functional Difficulty"]
    .sum().assign(
        Region=lambda x: x["Region"])
)
disability_by_region 

Disability  \
0           Visual Disability   
1           Visual Disability   
2           Visual Disability   
3           Visual Disability   
4           Visual Disability   
..                        ...   
301  Communication Disability   
302  Communication Disability   
303  Communication Disability   
304  Communication Disability   
305  Communication Disability   

                                                Region    Status  \
0                        National Capital Region (NCR)      Mild   
1                        National Capital Region (NCR)  Moderate   
2                        National Capital Region (NCR)    Severe   
3               Cordillera Administrative Region (CAR)      Mild   
4               Cordillera Administrative Region (CAR)  Moderate   
..                                                 ...       ...   
301                               Region XIII (Caraga)  Moderate   
302                               Region XIII (Caraga)    Severe   
303  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...      Mild   
304  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...  Moderate   
305  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...    Severe   

     Household Population 5 Years Old and Over with Functional Difficulty  
0                                               755747                     
1                                                46059                     
2                                                 6502                     
3                                                94626                     
4                                                 7733                     
..                                                 ...                     
301                                               4465                     
302                                               3708                     
303                                              22560                     
304                                               4410                     
305                                               3234                     

[306 rows x 4 columns]

In [ ]:
total_disability_population=pd.merge(disability_by_region,total_population_region,on="Region",how="left")
total_disability_population["Person affected by disability per 100k"]=np.ceil(total_disability_population['Household Population 5 Years Old and Over with Functional Difficulty']
                                                                       /total_disability_population['Population']
                                                                       * 100000)

def func(x):
    return total_disability_population.loc[total_disability_population["Status"]==str(x).capitalize().strip()]
func("mild") # will put in try catch later to catch errors like spelling and spacing as whre it can filter to certain disability

Disability  \
0           Visual Disability   
1           Visual Disability   
2           Visual Disability   
3           Visual Disability   
4           Visual Disability   
..                        ...   
301  Communication Disability   
302  Communication Disability   
303  Communication Disability   
304  Communication Disability   
305  Communication Disability   

                                                Region    Status  \
0                        National Capital Region (NCR)      Mild   
1                        National Capital Region (NCR)  Moderate   
2                        National Capital Region (NCR)    Severe   
3               Cordillera Administrative Region (CAR)      Mild   
4               Cordillera Administrative Region (CAR)  Moderate   
..                                                 ...       ...   
301                               Region XIII (Caraga)  Moderate   
302                               Region XIII (Caraga)    Severe   
303  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...      Mild   
304  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...  Moderate   
305  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...    Severe   

     Household Population 5 Years Old and Over with Functional Difficulty  \
0                                               755747                      
1                                                46059                      
2                                                 6502                      
3                                                94626                      
4                                                 7733                      
..                                                 ...                      
301                                               4465                      
302                                               3708                      
303                                              22560                      
304                                               4410                      
305                                               3234                      

     Population  Person affected by disability per 100k  
0      13804656                                  5475.0  
1      13804656                                   334.0  
2      13804656                                    48.0  
3       1807739                                  5235.0  
4       1807739                                   428.0  
..          ...                                     ...  
301     2753107                                   163.0  
302     2753107                                   135.0  
303     4183315                                   540.0  
304     4183315                                   106.0  
305     4183315                                    78.0  

[306 rows x 6 columns]

In [30]:
total_disability_func()

Disability  \
0           Visual Disability   
1           Visual Disability   
2           Visual Disability   
3           Visual Disability   
4           Visual Disability   
..                        ...   
301  Communication Disability   
302  Communication Disability   
303  Communication Disability   
304  Communication Disability   
305  Communication Disability   

                                                Region    Status  \
0                        National Capital Region (NCR)      Mild   
1                        National Capital Region (NCR)  Moderate   
2                        National Capital Region (NCR)    Severe   
3               Cordillera Administrative Region (CAR)      Mild   
4               Cordillera Administrative Region (CAR)  Moderate   
..                                                 ...       ...   
301                               Region XIII (Caraga)  Moderate   
302                               Region XIII (Caraga)    Severe   
303  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...      Mild   
304  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...  Moderate   
305  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...    Severe   

     Household Population 5 Years Old and Over with Functional Difficulty  \
0                                               755747                      
1                                                46059                      
2                                                 6502                      
3                                                94626                      
4                                                 7733                      
..                                                 ...                      
301                                               4465                      
302                                               3708                      
303                                              22560                      
304                                               4410                      
305                                               3234                      

     Population  Person affected by disability per 100k  
0      13804656                                  5475.0  
1      13804656                                   334.0  
2      13804656                                    48.0  
3       1807739                                  5235.0  
4       1807739                                   428.0  
..          ...                                     ...  
301     2753107                                   163.0  
302     2753107                                   135.0  
303     4183315                                   540.0  
304     4183315                                   106.0  
305     4183315                                    78.0  

[306 rows x 6 columns]

In [18]:
total_disability_population_pivot=total_disability_population.pivot_table(index=["Region","Status"],columns=["Disability"])
total_disability_population_pivot["Person affected by disability per 100k"]
# ok this is shit need to clean up 

Disability                                                   Visual Disability  \
Region                                             Status                        
BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANAO... Mild                 2720.0   
                                                   Moderate              145.0   
                                                   Severe                 90.0   
Cordillera Administrative Region (CAR)             Mild                 5235.0   
                                                   Moderate              428.0   
                                                   Severe                 76.0   
MIMAROPA Region                                    Mild                 8016.0   
                                                   Moderate              631.0   
                                                   Severe                 74.0   
National Capital Region (NCR)                      Mild                 5475.0   
                                                   Moderate              334.0   
                                                   Severe                 48.0   
REGION XI (DAVAO REGION)                           Mild                 5341.0   
                                                   Moderate              379.0   
                                                   Severe                 57.0   
REGION XII (SOCCSKSARGEN)                          Mild                 7049.0   
                                                   Moderate              492.0   
                                                   Severe                 81.0   
Region I (Ilocos Region)                           Mild                 6798.0   
                                                   Moderate              438.0   
                                                   Severe                 97.0   
Region II (Cagayan Valley)                         Mild                 7630.0   
                                                   Moderate              504.0   
                                                   Severe                 98.0   
Region III (Central Luzon)                         Mild                 6626.0   
                                                   Moderate              380.0   
                                                   Severe                 74.0   
Region IV-A (CALABARZON)                           Mild                 5444.0   
                                                   Moderate              323.0   
                                                   Severe                 53.0   
Region IX (Zamboanga Peninsula)                    Mild                 5363.0   
                                                   Moderate              371.0   
                                                   Severe                 67.0   
Region V (Bicol Region)                            Mild                 6560.0   
                                                   Moderate              493.0   
                                                   Severe                 77.0   
Region VI (Western Visayas)                        Mild                 6117.0   
                                                   Moderate              458.0   
                                                   Severe                 88.0   
Region VII (Central Visayas)                       Mild                 4694.0   
                                                   Moderate              376.0   
                                                   Severe                 81.0   
Region VIII (Eastern Visayas)                      Mild                 6531.0   
                                                   Moderate              479.0   
                                                   Severe                 82.0   
Region X (Northern Mindanao)                       Mild                 4427.0   
                                                   Moderate     

In [19]:
dataset["Region"].unique()

['National Capital Region (NCR)', 'Cordillera Administrative Region (CAR)', 'Region I (Ilocos Region)', 'Region II (Cagayan Valley)', 'Region III (Central Luzon)', ..., 'Region X (Northern Mindanao)', 'REGION XI (DAVAO REGION)', 'REGION XII (SOCCSKSARGEN)', 'Region XIII (Caraga)', 'BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDAN...]
Length: 17
Categories (17, object): ['National Capital Region (NCR)' < 'Cordillera Administrative Region (CAR)' < 'Region I (Ilocos Region)' < 'Region II (Cagayan Valley)' ... 'REGION XI (DAVAO REGION)' < 'REGION XII (SOCCSKSARGEN)' < 'Region XIII (Caraga)' < 'BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDAN...]

In [20]:
most_affected_age=(dataset.loc[(dataset["Sex"] == "Both Sexes") & (dataset["Status"] == "All")]
    .groupby(["Disability","Region"], as_index=False)[['Age: 5-19',"Age: 20-34","Age: 35–54","Age: 55-80+"]]
    .sum()
    )

#change maa_melted_filtered to a function to filter by like total functional difficulty where you take populaiton and 
#divide it becasue it seem to have more old than you 

In [21]:
age_regional_disibality=pd.merge(most_affected_age,total_population_region,on="Region",how="left")

age_group = {
    "5-19": "Age: 5-19",
    "20-34": "Age: 20-34",
    "35-54": "Age: 35–54",
    "55-80+": "Age: 55-80+"
}

for age_label, age_column in age_group.items():
    age_regional_disibality[f"average affected in Age: {age_label}"] = np.ceil(age_regional_disibality[age_column] / age_regional_disibality['Population'] * 100000)

def age_region_demo(x):
    return age_regional_disibality.loc[age_regional_disibality["Disability"]==str(x).capitalize().strip()]
age_region_demo("visual disability") 

# this just need optimization like not showing column that is not filter by average since its not importance anymore

Empty DataFrame
Columns: [Disability, Region, Age: 5-19, Age: 20-34, Age: 35–54, Age: 55-80+, Population, average affected in Age: 5-19, average affected in Age: 20-34, average affected in Age: 35-54, average affected in Age: 55-80+]
Index: []

In [22]:
age_regional_disibality

Disability  \
0           Visual Disability   
1           Visual Disability   
2           Visual Disability   
3           Visual Disability   
4           Visual Disability   
..                        ...   
97   Communication Disability   
98   Communication Disability   
99   Communication Disability   
100  Communication Disability   
101  Communication Disability   

                                                Region  Age: 5-19  Age: 20-34  \
0                        National Capital Region (NCR)      52614      110939   
1               Cordillera Administrative Region (CAR)       4414        9487   
2                             Region I (Ilocos Region)       7747       19293   
3                           Region II (Cagayan Valley)       6710       16371   
4                           Region III (Central Luzon)      35614       77051   
..                                                 ...        ...         ...   
97                        Region X (Northern Mindanao)       6565        5682   
98                            REGION XI (DAVAO REGION)       6169        5082   
99                           REGION XII (SOCCSKSARGEN)       8733        7187   
100                               Region XIII (Caraga)       4090        3222   
101  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...       5642        3795   

     Age: 35–54  Age: 55-80+  Population  average affected in Age: 5-19  \
0        261641       383114    13804656                          382.0   
1         28590        61235     1807739                          245.0   
2        114978       244393     5270807                          147.0   
3         98179       179795     3657746                          184.0   
4        292930       465966    12313714                          290.0   
..          ...          ...         ...                            ...   
97         5538        13390     5017050                          131.0   
98         5566        13543     5290867                          117.0   
99         7432        18995     4919935                          178.0   
100        3087         7837     2753107                          149.0   
101        5951        14816     4183315                          135.0   

     average affected in Age: 20-34  average affected in Age: 35-54  \
0                             804.0                          1896.0   
1                             525.0                          1582.0   
2                             367.0                          2182.0   
3                             448.0                          2685.0   
4                             626.0                          2379.0   
..                              ...                             ...   
97                            114.0                           111.0   
98                             97.0                           106.0   
99                            147.0                           152.0   
100                           118.0                           113.0   
101                            91.0                           143.0   

     average affected in Age: 55-80+  
0                             2776.0  
1                             3388.0  
2                             4637.0  
3                             4916.0  
4                             3785.0  
..                               ...  
97                             267.0  
98                             256.0  
99                             387.0  
100                            285.0  
101                            355.0  

[102 rows x 11 columns]

In [23]:
age_regional_disibality_pivot=age_regional_disibality.pivot_table(index="Region",columns="Disability").head(5)
#this is exactly how i want it but i was just it to filter more cleanly like get rid of some stuffa and mayby add some funtion
#and make this where you can filter by age,its better to make it a regex so that ecven if not complete it will still search

def age_region_pivot_demo(x):
    return age_regional_disibality_pivot[x]
age_region_pivot_demo("Age: 5-19") 

Disability                                          Visual Disability  \
Region                                                                  
BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANAO...             4100.0   
Cordillera Administrative Region (CAR)                         4414.0   
MIMAROPA Region                                                6569.0   
National Capital Region (NCR)                                 52614.0   
REGION XI (DAVAO REGION)                                       8333.0   

Disability                                          Hearing Disability  \
Region                                                                   
BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANAO...              1945.0   
Cordillera Administrative Region (CAR)                          1345.0   
MIMAROPA Region                                                 3182.0   
National Capital Region (NCR)                                   6729.0   
REGION XI (DAVAO REGION)                                        3285.0   

Disability                                          Mobility Disability  \
Region                                                                    
BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANAO...               2139.0   
Cordillera Administrative Region (CAR)                           1477.0   
MIMAROPA Region                                                  2939.0   
National Capital Region (NCR)                                    6487.0   
REGION XI (DAVAO REGION)                                         3401.0   

Disability                                          Cognitive Disability  \
Region                                                                     
BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANAO...                3090.0   
Cordillera Administrative Region (CAR)                            1662.0   
MIMAROPA Region                                                   2972.0   
National Capital Region (NCR)                                     8238.0   
REGION XI (DAVAO REGION)                                          4339.0   

Disability                                          Self-Care Disability  \
Region                                                                     
BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANAO...                8499.0   
Cordillera Administrative Region (CAR)                            1874.0   
MIMAROPA Region                                                   3478.0   
National Capital Region (NCR)                                    10019.0   
REGION XI (DAVAO REGION)                                          5313.0   

Disability                                          Communication Disability  
Region                                                                        
BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANAO...                    5642.0  
Cordillera Administrative Region (CAR)                                2146.0  
MIMAROPA Region                                                       4473.0  
National Capital Region (NCR)                                        11884.0  
REGION XI (DAVAO REGION)                                              6169.0

In [24]:
gender_severety=(dataset.loc[(dataset["Sex"] != 'Both Sexes')& (dataset["Status"] != 'All')]
                 .groupby(["Region","Sex","Disability","Status"],as_index=False)
                 ["Household Population 5 Years Old and Over with Functional Difficulty"]
                 .sum())



gender_serverity_disability=pd.merge(gender_severety,total_population_region,on="Region",how="left").assign(population=lambda x:x["Population"]/2)
gender_serverity_disability["Gender affected by disability per 100k"]=(gender_serverity_disability["Household Population 5 Years Old and Over with Functional Difficulty"]/(gender_serverity_disability['Population']/2)*100000).astype(int)
#gender_serverity_disability.rename(columns={"Population":"Total Population"},inplace=True)
gender_serverity_disability.rename(columns={"population":"Gender Population"},inplace=True)
gender_serverity_disability
#just do what you do to other

Region     Sex  \
0                        National Capital Region (NCR)  Female   
1                        National Capital Region (NCR)  Female   
2                        National Capital Region (NCR)  Female   
3                        National Capital Region (NCR)  Female   
4                        National Capital Region (NCR)  Female   
..                                                 ...     ...   
607  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...    Male   
608  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...    Male   
609  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...    Male   
610  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...    Male   
611  BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANA...    Male   

                   Disability    Status  \
0           Visual Disability      Mild   
1           Visual Disability  Moderate   
2           Visual Disability    Severe   
3          Hearing Disability      Mild   
4          Hearing Disability  Moderate   
..                        ...       ...   
607      Self-Care Disability  Moderate   
608      Self-Care Disability    Severe   
609  Communication Disability      Mild   
610  Communication Disability  Moderate   
611  Communication Disability    Severe   

     Household Population 5 Years Old and Over with Functional Difficulty  \
0                                               444800                      
1                                                27516                      
2                                                 3376                      
3                                                72315                      
4                                                 7042                      
..                                                 ...                      
607                                               1785                      
608                                               1326                      
609                                              11403                      
610                                               1847                      
611                                               1297                      

     Population  Gender Population  Gender affected by disability per 100k  
0      13804656          6902328.0                                    6444  
1      13804656          6902328.0                                     398  
2      13804656          6902328.0                                      48  
3      13804656          6902328.0                                    1047  
4      13804656          6902328.0                                     102  
..          ...                ...                                     ...  
607     4183315          2091657.5                                      85  
608     4183315          2091657.5                                      63  
609     4183315          2091657.5                                     545  
610     4183315          2091657.5                                      88  
611     4183315          2091657.5                                      62  

[612 rows x 8 columns]

In [25]:

gender_serverity_disability_pivot=gender_serverity_disability.pivot_table(index=["Region","Sex","Status"],columns=["Disability"])
gender_serverity_disability_pivot["Gender affected by disability per 100k"]
#drop other column just get this column but only for this pivot

Disability                                                          Visual Disability  \
Region                                             Sex    Status                        
BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANAO... Female Mild                 2742.0   
                                                          Moderate              155.0   
                                                          Severe                 91.0   
                                                   Male   Mild                 2696.0   
                                                          Moderate              134.0   
...                                                                               ...   
Region XIII (Caraga)                               Female Moderate              441.0   
                                                          Severe                 70.0   
                                                   Male   Mild                 4700.0   
                                                          Moderate              355.0   
                                                          Severe                 57.0   

Disability                                                          Hearing Disability  \
Region                                             Sex    Status                         
BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANAO... Female Mild                  1305.0   
                                                          Moderate                91.0   
                                                          Severe                  14.0   
                                                   Male   Mild                  1295.0   
                                                          Moderate                81.0   
...                                                                                ...   
Region XIII (Caraga)                               Female Moderate               227.0   
                                                          Severe                  62.0   
                                                   Male   Mild                  1576.0   
                                                          Moderate               234.0   
                                                          Severe                  69.0   

Disability                                                          Mobility Disability  \
Region                                             Sex    Status                          
BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANAO... Female Mild                   1277.0   
                                                          Moderate                120.0   
                                                          Severe                   25.0   
                                                   Male   Mild                   1217.0   
                                                          Moderate                105.0   
...                                                                                 ...   
Region XIII (Caraga)                               Female Moderate                289.0   
                                                          Severe                  153.0   
                                                   Male   Mild                   1295.0   
                                                          Moderate                304.0   
                                                          Severe                  139.0   

Disability                                                          Cognitive Disability  \
Region                                             Sex    Status                           
BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANAO... Female Mild                    1032.0   
                                                          Moderate                  89.0   
                                                          Severe                    18.0   
                           

In [26]:
most_common_disability_region=(dataset.loc[(dataset["Sex"] == 'Both Sexes')& (dataset["Status"] == 'All')]
                 .groupby(["Region","Disability"],as_index=False)
                 ["Household Population 5 Years Old and Over with Functional Difficulty"]
                 .sum())


most_common_disability_region_pivot=most_common_disability_region.pivot_table(index=["Region"],aggfunc="max")
most_common_disability_region_pivot

Disability  \
Region                                                                         
National Capital Region (NCR)                       Communication Disability   
Cordillera Administrative Region (CAR)              Communication Disability   
Region I (Ilocos Region)                            Communication Disability   
Region II (Cagayan Valley)                          Communication Disability   
Region III (Central Luzon)                          Communication Disability   
Region IV-A (CALABARZON)                            Communication Disability   
MIMAROPA Region                                     Communication Disability   
Region V (Bicol Region)                             Communication Disability   
Region VI (Western Visayas)                         Communication Disability   
Region VII (Central Visayas)                        Communication Disability   
Region VIII (Eastern Visayas)                       Communication Disability   
Region IX (Zamboanga Peninsula)                     Communication Disability   
Region X (Northern Mindanao)                        Communication Disability   
REGION XI (DAVAO REGION)                            Communication Disability   
REGION XII (SOCCSKSARGEN)                           Communication Disability   
Region XIII (Caraga)                                Communication Disability   
BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANAO...  Communication Disability   

                                                    Household Population 5 Years Old and Over with Functional Difficulty  
Region                                                                                                                    
National Capital Region (NCR)                                                                  808308                     
Cordillera Administrative Region (CAR)                                                         103726                     
Region I (Ilocos Region)                                                                       386411                     
Region II (Cagayan Valley)                                                                     301055                     
Region III (Central Luzon)                                                                     871561                     
Region IV-A (CALABARZON)                                                                       934301                     
MIMAROPA Region                                                                                276850                     
Region V (Bicol Region)                                                                        437299                     
Region VI (Western Visayas)                                                                    526591                     
Region VII (Central Visayas)                                                                   409749                     
Region VIII (Eastern Visayas)                                                                  336263                     
Region IX (Zamboanga Peninsula)                                                                219365                     
Region X (Northern Mindanao)                                                                   241773                     
REGION XI (DAVAO REGION)                                                                       305550                     
REGION XII (SOCCSKSARGEN)                                                                      374882                     
Region XIII (Caraga)                                                                           158468                     
BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANAO...                                             123235

In [27]:

np.ceil(most_common_disability_region.pivot_table(index=["Region"],
                                                    aggfunc={"Household Population 5 Years Old and Over with Functional Difficulty":["min", "max", "mean"]}))

Household Population 5 Years Old and Over with Functional Difficulty  \
                                                                                                                    max   
Region                                                                                                                    
National Capital Region (NCR)                                                                  808308                     
Cordillera Administrative Region (CAR)                                                         103726                     
Region I (Ilocos Region)                                                                       386411                     
Region II (Cagayan Valley)                                                                     301055                     
Region III (Central Luzon)                                                                     871561                     
Region IV-A (CALABARZON)                                                                       934301                     
MIMAROPA Region                                                                                276850                     
Region V (Bicol Region)                                                                        437299                     
Region VI (Western Visayas)                                                                    526591                     
Region VII (Central Visayas)                                                                   409749                     
Region VIII (Eastern Visayas)                                                                  336263                     
Region IX (Zamboanga Peninsula)                                                                219365                     
Region X (Northern Mindanao)                                                                   241773                     
REGION XI (DAVAO REGION)                                                                       305550                     
REGION XII (SOCCSKSARGEN)                                                                      374882                     
Region XIII (Caraga)                                                                           158468                     
BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANAO...                                             123235                     

                                                                     
                                                        mean    min  
Region                                                               
National Capital Region (NCR)                       221749.0  60064  
Cordillera Administrative Region (CAR)               41608.0  11904  
Region I (Ilocos Region)                            126650.0  33612  
Region II (Cagayan Valley)                           98339.0  23981  
Region III (Central Luzon)                          247132.0  61405  
Region IV-A (CALABARZON)                            274965.0  75083  
MIMAROPA Region                                      89848.0  22211  
Region V (Bicol Region)                             151157.0  41595  
Region VI (Western Visayas)                         189653.0  57685  
Region VII (Central Visayas)                        155739.0  51846  
Region VIII (Eastern Visayas)                       117579.0  31056  
Region IX (Zamboanga Peninsula)                      77885.0  24612  
Region X (Northern Mindanao)                         88683.0  31175  
REGION XI (DAVAO REGION)                            101367.0  30360  
REGION XII (SOCCSKSARGEN)                           134762.0  42347  
Region XIII (Caraga)                                 57988.0  17927  
BANGSAMORO AUTONOMOUS REGION IN MUSLIM MINDANAO...   58714.0  30204

ok am done i just to maek it even more better with this now i jsut need to create visualization then put that in a website then maybe comback to this and do more analysis like advancce one then pust it as a seprate repo or i could combine both but  i need to finish then 

In [28]:

dataset.to_csv(r"csv/final_FDD.csv",index=False)